In [1]:
from utils import *



In [2]:
import ee

ee.Initialize()

In [128]:
def getFeatureRaster(feature, exclusionRaster, targetRaster):
    excls = exclusionRaster.clip(feature)
    targ = targetRaster.clip(feature)

    return targ.multiply(excls)

In [129]:
def reduceToArea(image):
    areaDict = image.pixelArea().reduceRegion(ee.Reducer.sum(), scale=140, geometry=image.geometry())
    area = ee.Number(areaDict.get('area')).divide(1e6)
    name = image.get("name")
    newFeat = ee.Feature(image.geometry())
    newFeat = newFeat.set({'area':area, 'name':name})
    #newFeat = ee.Feature.setGeometry()
    return newFeat

In [143]:
# Scenario 1 - Max Exclusions


common = getExclusions()
wind = getExclusions("wind")
solar = getExclusions("solar")


#Scenario 1 - Max Exclusions
MaxWindExclusions = common + wind
MaxSolarExclusions = common + solar

maxExcl = {"wind":MaxWindExclusions, "solar": MaxSolarExclusions}

#Scenario 2 - Med Exclusions: 
MedWindExclusions = common + wind
MedWindExclusions.remove("Peatland")
MedWindExclusions.remove("Areas of Natural Beauty")

MedSolarExclusions = common + solar
MedSolarExclusions.remove("Peatland")
MedSolarExclusions.remove("Areas of Natural Beauty")

medExcl = {"wind":MedWindExclusions, "solar": MedSolarExclusions}

#Scenario 3 - Min Exclusions
MinWindExclusions = common + wind
MinWindExclusions.remove("Peatland")
MinWindExclusions.remove("Areas of Natural Beauty")
MinWindExclusions.remove("England National Parks")
MinWindExclusions.remove("Scotland Scenic Areas")
MinWindExclusions.remove("Wales National Park")

MinSolarExclusions = common + solar
MinSolarExclusions.remove("Peatland")
MinSolarExclusions.remove("Areas of Natural Beauty")
MinSolarExclusions.remove("England National Parks")
MinSolarExclusions.remove("Scotland Scenic Areas")
MinSolarExclusions.remove("Wales National Park")

minExcl = {"wind":MinWindExclusions, "solar": MinSolarExclusions}


paramsDict = {"min":minExcl, "med":medExcl, "max": maxExcl}


def getPowerLocal(geometry, exclusions, power):
    localPower = power.multiply(exclusions).clip(geometry)
    return localPower

exDict = getExclusionsDict()
resultsDict = {}
paramList = list(paramsDict.keys())

for exp in paramList:
    
    areaRast = ee.Image.constant(1)
    windExc = paramsDict[exp]['wind']
    solarExc = paramsDict[exp]['solar']
    print(solarExc)
    assert windExc != solarExc

    windExclusions = [exDict[x] for x in windExc]
    solarExclusions = [exDict[x] for x in solarExc]

    windExclusions = compute_exclusions(windExclusions)
    solarExclusions = compute_exclusions(solarExclusions)

    featCol = constituenciesVector()



    solarAreaImgCol = ee.ImageCollection(featCol.map(lambda x: getFeatureRaster(x, solarExclusions, areaRast).set("name", ee.String(x.get('pcon19nm'))) ))
    windAreaImgCol = ee.ImageCollection(featCol.map(lambda x: getFeatureRaster(x, windExclusions, areaRast).set("name", ee.String(x.get('pcon19nm'))) ))

    #windAreaImgCol = windAreaImgCol.updateMask(solarAreaImgCol.gte(1))

    windAreaReduced = windAreaImgCol.map(reduceToArea)
    windarr = windAreaReduced.aggregate_array('area').getInfo()
    windNames = windAreaReduced.aggregate_array('name').getInfo()
    windPFrame = pd.DataFrame(windarr, index=windNames, columns=["Wind Area (KM^2)"])

    solarAreaReduced = solarAreaImgCol.map(reduceToArea)
    solarr = solarAreaReduced.aggregate_array('area').getInfo()
    solNames = solarAreaReduced.aggregate_array('name').getInfo()
    solPFrame = pd.DataFrame(solarr, index=solNames, columns=["Solar Area (KM^2)"])

    potentialFrame = solPFrame.join(windPFrame)
    assert solarr != windarr
    resultsDict[exp] = potentialFrame


['Roads', 'Railway', 'Protected Areas', 'Woodlands', 'Cycle Paths', 'Surface Water', 'Cultural Sites', 'Parks and Green Space', 'Functional Sites', 'Slope > 10', 'Existing Solar PV', 'Agricultural Land']
['Roads', 'Railway', 'Protected Areas', 'Woodlands', 'Cycle Paths', 'Surface Water', 'Cultural Sites', 'Parks and Green Space', 'Functional Sites', 'England National Parks', 'Scotland Scenic Areas', 'Wales National Park', 'Slope > 10', 'Existing Solar PV', 'Agricultural Land']
['Roads', 'Railway', 'Peatland', 'Protected Areas', 'Areas of Natural Beauty', 'Woodlands', 'Cycle Paths', 'Surface Water', 'Cultural Sites', 'Parks and Green Space', 'Functional Sites', 'England National Parks', 'Scotland Scenic Areas', 'Wales National Park', 'Slope > 10', 'Existing Solar PV', 'Agricultural Land']


In [144]:
solarExcmin = paramsDict["min"]['solar']
solarExcmax = paramsDict["max"]['solar']
solExclMin = [exDict[x] for x in solarExcmin]
solExclMax = [exDict[x] for x in solarExcmax]

In [145]:
solExclMin == solExclMax

False

In [141]:
solarExcmax

['Roads',
 'Railway',
 'Peatland',
 'Protected Areas',
 'Areas of Natural Beauty',
 'Woodlands',
 'Cycle Paths',
 'Surface Water',
 'Cultural Sites',
 'Parks and Green Space',
 'Functional Sites',
 'England National Parks',
 'Scotland Scenic Areas',
 'Wales National Park',
 'Slope > 10',
 'Existing Solar PV',
 'Agricultural Land']

In [106]:
constVect.first().get('pcon19nm').getInfo()

'East Antrim'

In [103]:
constVect.map(lambda x: getPowerLocal(x, solarExclusions, areaRast)).getInfo()

{'type': 'ImageCollection',
 'bands': [],
 'version': 1657720329134978,
 'id': 'projects/data-sunlight-311713/assets/Westminster_Parliamentary_Constituencies_December_2019_Boundaries_UK_BUC',
 'properties': {'system:asset_size': 696696},
 'features': [{'type': 'Image',
   'bands': [{'id': 'constant',
     'data_type': {'type': 'PixelType',
      'precision': 'int',
      'min': 0,
      'max': 1},
     'dimensions': [1935, 1740],
     'origin': [625590, 17432],
     'crs': 'EPSG:4326',
     'crs_transform': [0.0002777777777777778,
      0,
      -180.0001388888889,
      0,
      -0.0002777777777777778,
      60.00013888888889]}],
   'properties': {'system:footprint': {'type': 'Polygon',
     'coordinates': [[[-5.8955367408592245, 54.674812130734885],
       [-5.868255479205339, 54.68953242304108],
       [-5.857115106889868, 54.69411612905294],
       [-5.847856684301377, 54.697924473817665],
       [-5.836801396439479, 54.70696362419304],
       [-5.823520892915557, 54.71101799731961

In [101]:
solarr == windarr

True

True

In [92]:
solarr 

[585543.5513324095,
 396985.7103379482,
 2079793.1446116462,
 266625.54456078407,
 504074.650430629,
 19790.355716341142,
 115161.83571582803,
 136126.03938920415,
 94597.42551663992,
 26691.451539824622,
 262914.78763092845,
 109364.02879363895,
 1242887.6239376096,
 8724.762993887865,
 55222.77697843901,
 2096839.549968471,
 25704.051918443623,
 29398.348009424768,
 17289.339600325497,
 680215.1811938052,
 82753.47961798793,
 38130.598630778964,
 19717.380656024045,
 60401.350294435506,
 1199237.7246691363,
 17875.323641367962,
 15922.308955564495,
 772056.9789249997,
 226844.7526965802,
 79870.17368199678,
 54703.57242372853,
 48670.7557550704,
 18475.522662454045,
 247847.06710866248,
 1414219.1111318886,
 175857.090868309,
 11070.100629928767,
 1380442.8344767564,
 46896.698861331985,
 92338.97241047028,
 229747.60778872558,
 110870.26482502307,
 728162.8923982388,
 29933.136054151342,
 750891.9947862024,
 124801.70980302164,
 72634.89482249148,
 203776.95511991813,
 645619.031646

True

In [42]:
areaReduced.first().getInfo()

EEException: Collection.map: A mapped algorithm must return a Feature or Image.